
## 🧠 **Monday Theme:** *“Code as Protocol, Folder as Ethic”*

> *"Drop this .do file and your .dta into a folder. Click run. It’ll do the rest."*
> That’s what a **non-Stata data guardian** needs.
> It creates an *ethical workspace*, keeps outputs contained, and produces **verifiable artifacts**: logs, tables, plots.

---

## 🏗️ Folder Architecture (Scaffold for All Projects)

```
project/
├── code/           # .do files
│   └── lab5_template.do
├── data/           # .dta files go here
├── output/         # Graphs, logs, tables
├── notes/          # README, variable dictionary, protocols
└── master.do       # Calls everything in code/
```

---

## 🔹 `lab5_template.do` (for students — ready to fill in)

```stata

************************************************************
* lab5.do - Self-organizing portable lab file (needs debugging)
************************************************************

clear all
set more off

* 1. Define root folder
local root = c(pwd)

* 2. Define folder paths
local data   "`root'/data"
local output "`root'/output"
local code   "`root'/code"
local notes  "`root'/notes"

* 3. Create folders
capture mkdir "`data'"
capture mkdir "`output'"
capture mkdir "`code'"
capture mkdir "`notes'"

* 4. Move all .dta files into /data/
local dtafiles : dir "`root'" files "*.dta"
foreach f of local dtafiles {
    local src "`root'/`f'"
    local dest "`data'/`f'"
    copy "`src'" "`dest'", replace
    erase "`src'"
}

* 5. Change directory to /data
cd "`data'"

* 6. Start log
log using "`output'/lab5_output.log", replace

* 7. Load and merge data
use transplants.dta, clear
merge 1:1 fake_id using donors_recipients.dta
drop if _merge != 3

* 8. Create variables
gen over50 = age > 50
gen f_time = end_d - transplant_d
format transplant_d end_d %td
stset f_time, failure(died)

* 9. Graph
sts graph, by(over50)
graph export "`output'/survival_over50.png", replace

* 10. Close log
log close


```

<details>
    <summary>v1.1</summary>

```stata
************************************************************
* lab5.do - Self-organizing portable lab file  
************************************************************

clear all
set more off

* 1. Define root folder
local root = c(pwd)

* 2. Define folder paths
local data   "`root'/data"
local output "`root'/output"
local code   "`root'/code"
local notes  "`root'/notes"

* 3. Create folders
capture mkdir "`data'"
capture mkdir "`output'"
capture mkdir "`code'"
capture mkdir "`notes'"

* 4. Move all .dta files into /data/
local dtafiles : dir "`root'" files "*.dta"
foreach f of local dtafiles {
    local src "`root'/`f'"
    local dest "`data'/`f'"
    copy "`src'" "`dest'", replace
    erase "`src'"
}

* 5. Change directory to /data
//cd "`data'"

* 6. Start log
capture drop _all
log using "`output'/lab5_output.log", replace

* 7. Load and merge data
use "`data'/transplants.dta", clear
merge 1:1 fake_id using data/donors_recipients.dta
drop if _merge != 3

* 8. Create variables
gen over50 = age > 50
gen f_time = end_d - transplant_d
format transplant_d end_d %td
stset f_time, failure(died)

* 9. Graph
sts graph, by(over50)
graph export "`output'/survival_over50.png", replace

* 10. Close log
log close
display "✅ All done. No errors. Outputs created."
```

</details>

<details>
    <summary>v1.2</summary>

```stata
* ************************************************************
* lab5_template.do - Self-organizing, reproducible lab file
* Designed for OS-agnostic use + graceful handoff to others
* ************************************************************

clear all
set more off

* 🌊 INIT: Declare root & core folders (relative to current location)
local root = c(pwd)
foreach folder in data output code notes {
    local `folder' "`root'/`folder'"
    capture mkdir ``folder''
}

* ❤️ COMMIT: Move all .dta files into /data/ so it's clean + modular
local dtafiles : dir "`root'" files "*.dta"
foreach f of local dtafiles {
    local src  "`root'/`f'"
    local dest "`data'/`f'"
    copy "`src'" "`dest'", replace
    erase "`src'"
}

* 🌀 FORK: Create structure for logging & error checking
capture drop _all
log using "`output'/lab5_output.log", replace

* 🐬 BRANCH: Load and prepare data
use "`data'/transplants.dta", clear
merge 1:1 fake_id using "`data'/donors_recipients.dta"
drop if _merge != 3

* 🔁 MERGE: Create variables, apply formats, and set survival time
gen over50 = age > 50
gen f_time = end_d - transplant_d
format transplant_d end_d %td
stset f_time, failure(died)

* 📊 OUTPUT: Graph and export results
sts graph, by(over50)
graph export "`output'/survival_over50.png", replace

* ✅ CLOSE: Log and finish
log close
display "✅ All done. No errors. Outputs created."

```

</details>


<details>
    <summary>v1.3</summary>

```stata

/**************************************************************************
 🔁 just-click.do – Self-organizing, reproducible lab file
     ▸ OS-agnostic
     ▸ Modular folder structure
     ▸ Canonical symbolic stages: INIT → COMMIT → FORK → BRANCH → MERGE → OUTPUT
**************************************************************************/

clear all
set more off

* 🌐 Set global slash (optional – only needed for shell calls)
if c(os) == "Windows" {
    global SL "\"
}
else {
    global SL "/"
}

* 🌊 INIT: Define root + core folders (relative to current location)
global root = c(pwd)
foreach folder in data output code notes {
    local fpath = "$root/${SL}`folder'"
    capture mkdir "`fpath'"
    global `folder' "`fpath'"
}

* ❤️ COMMIT: Move all .dta files into /data for cleanliness
local dtafiles : dir "$root" files "*.dta"
foreach f of local dtafiles {
    local src  "$root/${SL}`f'"
    local dest "$data/${SL}`f'"
    copy "`src'" "`dest'", replace
    erase "`src'"
}

* 🌀 FORK: Setup logging and clear memory
capture drop _all
log using "$output${SL}lab5_output.log", replace

* 🐬 BRANCH: Load and prep data
use "$data${SL}transplants.dta", clear
merge 1:1 fake_id using "$data${SL}donors_recipients.dta"
drop if _merge != 3

* 🔁 MERGE: Generate variables, set time-to-event
gen over50 = age > 50
gen f_time = end_d - transplant_d
format transplant_d end_d %td
stset f_time, failure(died)

* 📊 OUTPUT: Graph results
sts graph, by(over50)
graph export "$output${SL}survival_over50.png", replace

* ✅ CLOSE: Done
log close
noi di as result "✅ All done. No errors. Outputs created."

```

</details>

---

## 🔸 `master.do` (for non-Stata collaborator to run)

```stata
************************************************************
*  master.do - Safe and Reproducible Entry Point
*  For: Non-Stata collaborators, remote collaborators
************************************************************

* Detect current directory
cd "`c(pwd)'"

* Create subfolders if needed
cap mkdir data
cap mkdir code
cap mkdir output
cap mkdir notes

* Reminder
di "✅ Project folders ready. Now place .dta files in /data, .do files in /code"

* Run lab5 template if it exists
cap do code/lab5_template.do
```

---

## 💡 Teaching Objectives for Monday

| Skill                  | Why It Matters                      |
| ---------------------- | ----------------------------------- |
| Folder discipline      | Prevents sprawl and broken links    |
| `cd`, `mkdir`, `local` | Teaches controlled automation       |
| Logging                | Accountability and reproducibility  |
| `master.do`            | Separates execution from authoring  |
| Relative paths         | Works across systems (Mac/PC/Linux) |
| Clear entry point      | Makes your collaborator feel safe   |

---

## 🛡️ Key Metaphor

> *The folder is your lab bench. The `.do` file is your protocol. The log is your lab notebook. The graph is your publication. Don’t contaminate.*

 
